In [ ]:
#task8.对于作业5中的星系，依据fits图像画出其一维的表面亮度轮廓，并计算其星等
#• 注意流量单位
#• 一维轮廓：
        #✓椭圆测光：椭圆是等面亮度轮廓，半径沿着长轴方向
        #✓圆测光: 圆孔径内的平均表面亮度
#• 星等：
     #✓积分（求和）到某个等亮度半径处
     #✓根据面亮度轮廓模型，积分到无穷远处
import numpy as np
import matplotlib.pyplot as plt
from astropy.io import fits
from photutils.isophote import Ellipse, EllipseGeometry, build_ellipse_model

# 加载FITS文件
file_path = '149.74358_2.125144_sci.fits'  # 替换为你的FITS文件路径


with fits.open(file_path) as hdul:
    hdul.info()
    image_data = hdul[1].data

import numpy as np
import matplotlib.pyplot as plt
from astropy.io import fits
from photutils.detection import find_peaks
from photutils.isophote import EllipseGeometry, Ellipse

# 1. 加载FITS文件并提取图像数据
file_path = '149.74358_2.125144_sci.fits'  # 替换为你的FITS文件路径
with fits.open(file_path) as hdul:
    image_data = hdul[1].data

# 检查 image_data 是否为空
if image_data is None:
    raise ValueError("图像数据未正确加载，请检查FITS文件。")

# 2. 提取亮点区域
# 设定一个阈值来检测亮点
threshold = np.percentile(image_data, 99)  # 选择99%亮度作为阈值（可调整）

# 使用 photutils 的 find_peaks 函数来查找亮点
peaks = find_peaks(image_data, threshold=threshold)

# 3. 绘制原始图像和亮点区域
plt.figure(figsize=(8, 8))
plt.imshow(image_data, origin='lower', cmap='gray', vmin=np.min(image_data), vmax=np.max(image_data))
plt.colorbar()
plt.title("原始图像及亮点区域")

# 标出亮点区域
plt.scatter(peaks['x_peak'], peaks['y_peak'], color='red', label='Peak locations', marker='x')
plt.legend()
plt.show()

# 4. 选择第一个亮点区域进行椭圆拟合
# 假设第一个亮点是我们的目标
x_center, y_center = peaks['x_peak'][0], peaks['y_peak'][0]

# 定义椭圆拟合的初始参数
sma = 10  # 半长轴（以像素为单位）
eps = 0.1  # 离心率
pa = 0.0  # 位置角（以弧度为单位）

# 创建椭圆几何体
geometry = EllipseGeometry(x0=x_center, y0=y_center, sma=sma, eps=eps, pa=pa)

# 使用 Ellipse 进行拟合
ellipse = Ellipse(image_data, geometry)
isolated_fits = ellipse.fit_isophote(sma)

# 5. 绘制拟合的椭圆轮廓
plt.figure(figsize=(8, 8))
plt.imshow(image_data, origin='lower', cmap='gray', vmin=np.min(image_data), vmax=np.max(image_data))
plt.colorbar()
plt.title("椭圆轮廓拟合")

# 获取拟合椭圆的坐标，使用 isolated_fits.sample.x 和 isolated_fits.sample.y
sample = isolated_fits.sample

# 从椭圆样本中提取 x 和 y 坐标
x_coords = sample.x
y_coords = sample.y

# 绘制拟合的椭圆轮廓
plt.plot(x_coords, y_coords, color='red')

# 标出亮点位置
plt.scatter(peaks['x_peak'], peaks['y_peak'], color='blue', label='Peak locations', marker='x')
plt.legend()
plt.show()


In [1]:
#作业9
import numpy as np
m = 25
M = -3
sigma_m = 0.1
Rv = 3.1
E_BV = 0.2
sigma_E_BV = 0.05

A_v = Rv * E_BV
m_corrected = m - A_v

distance_parsecs = 10 ** ((m_corrected - M + 5) / 5)

sigma_Av = Rv * sigma_E_BV
sigma_m_corrected = np.sqrt(sigma_m**2 + sigma_Av**2)
sigma_distance_parsecs = (distance_parsecs / 5) * sigma_m_corrected

print(f"Distance in pc: {distance_parsecs:.2f} +/- {sigma_distance_parsecs:.2f}")

Distance in pc: 2992264.64 +/- 110389.83


In [ ]:
#作业10
from astropy.cosmology import FlatLambdaCDM
cosmo = FlatLambdaCDM(H0=10, Om0=0.28)

halpha = 6563
halpha_z = 7000
z = halpha_z / halpha - 1

D_L = cosmo.luminosity_distance(z).value
D_L_pc = D_L * 1e6  # 转换为pc
flux = 0.6 * (6700 - 5500) * 1e-10  # 1e-10用于转换为erg/s/cm^2
AB_mag=20
M_r = AB_mag - 5 * (np.log10(D_L_pc) - 1) - 2.5 * np.log10(flux)  # 将D_L转换为pc
M_r
